<a href="https://colab.research.google.com/github/BrutFab/ppo_BipedalWalker_v3/blob/main/ppo_BipedalWalker_v3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **1. Setup**


### **Install Packages**

In [1]:
# Install necessary packages
!apt install swig cmake ffmpeg xvfb python3-opengl
!pip install stable-baselines3==2.0.0a5 gymnasium[box2d] huggingface_sb3 pyvirtualdisplay imageio[ffmpeg]

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
cmake is already the newest version (3.22.1-1ubuntu1.22.04.2).
ffmpeg is already the newest version (7:4.4.2-0ubuntu0.22.04.1).
The following additional packages will be installed:
  freeglut3 libfontenc1 libglu1-mesa libxfont2 libxkbfile1 swig4.0 x11-xkb-utils xfonts-base
  xfonts-encodings xfonts-utils xserver-common
Suggested packages:
  libgle3 python3-numpy swig-doc swig-examples swig4.0-examples swig4.0-doc
The following NEW packages will be installed:
  freeglut3 libfontenc1 libglu1-mesa libxfont2 libxkbfile1 python3-opengl swig swig4.0
  x11-xkb-utils xfonts-base xfonts-encodings xfonts-utils xserver-common xvfb
0 upgraded, 14 newly installed, 0 to remove and 45 not upgraded.
Need to get 9,753 kB of archives.
After this operation, 25.6 MB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy/universe amd64 freeglut3 amd64 2.8.1-6 [74.0 kB]
Get:2 http://

The Next Cell will force the notebook runtime to restart. This is to ensure all the new libraries installed will be used.

In [ ]:
import os
os.kill(os.getpid(), 9)

### **Start Virtual Display**

In [1]:
from pyvirtualdisplay import Display
virtual_display = Display(visible=0, size=(1400, 900))
virtual_display.start()

### **Setup Environment**

In [2]:
import gymnasium as gym
env = gym.make("BipedalWalker-v3", hardcore=True)
env.reset()

(array([ 2.7457748e-03,  1.0796259e-05, -1.4077756e-03, -1.6000072e-02,
         9.2496596e-02,  3.2680645e-03,  8.5978174e-01, -1.1957098e-03,
         1.0000000e+00,  3.2809932e-02,  3.2679352e-03,  8.5353220e-01,
        -2.2236530e-03,  1.0000000e+00,  4.4081339e-01,  4.4581950e-01,
         4.6142212e-01,  4.8954949e-01,  5.3410202e-01,  6.0246021e-01,
         7.0914787e-01,  8.8593054e-01,  9.7504026e-01,  1.0000000e+00],
       dtype=float32),
 {})

### **Observation Space**
Observation Space Shape (24,) vector of size 24, where each value contains different information about the walker:

- **Hull Angle Speed**: The speed at which the main body of the walker is rotating.
- **Angular Velocity**: The rate of change of the angular position of the walker.
- **Horizontal Speed**: The speed at which the walker is moving horizontally.
- **Vertical Speed**: The speed at which the walker is moving vertically.
- **Position of Joints**: The positions (angles) of the walker's joints. Given that the walker has 4 joints, this take up 4 values.
- **Joints Angular Speed**: The rate of change of the angular position for each joint. Again, this would be 4 values for the 4 joints.
- **Legs Contact with Ground**: Indicating whether each leg is in contact with the ground. Given two legs, this contains 2 values.
- **10 Lidar Rangefinder Measurements**: These are distance measurements to detect obstacles or terrain features around the walker. There are 10 of these values.


In [3]:
print("_____OBSERVATION SPACE_____ \n")
print("Observation Space Shape", env.observation_space.shape)
print("Sample observation", env.observation_space.sample()) # Get a random observation

_____OBSERVATION SPACE_____ 

Observation Space Shape (24,)
Sample observation [-0.45614123  2.8879125   2.6456494  -4.8847394  -0.5782697  -4.141727
 -1.4128497  -4.398258    2.2688951   0.9695038  -1.3905146  -0.13533457
 -1.280362    0.16277842  0.55950814 -0.54326314 -0.07042317  0.9742654
  0.6668436  -0.47779897 -0.15802848 -0.55885684 -0.98828036  0.717018  ]


### **Action Space**

 Actions are motor speed values in the [-1, 1] range for each of the 4 joints at both hips and knees.

In [4]:
print("\n _____ACTION SPACE_____ \n")
print("Action Space Shape", env.action_space.shape)
print("Action Space Sample", env.action_space.sample()) # Take a random action


 _____ACTION SPACE_____ 

Action Space Shape (4,)
Action Space Sample [-0.25526306  0.1981408  -0.6381555   0.6515663 ]


### **Vectorized Environment**
Create a vectorized environment (a method for stacking multiple independent environments into a single environment) of 16 environments to have more diverse experiences.

In [5]:
from stable_baselines3.common.env_util import make_vec_env
env = make_vec_env('BipedalWalker-v3', n_envs=16)

# **2. Building the Model**

In [6]:
from stable_baselines3 import PPO
model = PPO(
    policy = 'MlpPolicy',
    env = env,
    n_steps = 2048,
    batch_size = 128,
    n_epochs = 6,
    gamma = 0.999,
    gae_lambda = 0.98,
    ent_coef = 0.01,
    verbose=1)

Using cuda device


# 3.**Video Generation**

In [7]:
from wasabi import Printer
import numpy as np
from stable_baselines3.common.base_class import BaseAlgorithm
from pathlib import Path
import tempfile
from stable_baselines3.common.monitor import Monitor
from stable_baselines3.common.vec_env import (
    DummyVecEnv,
    VecEnv,
    VecVideoRecorder,
)

In [8]:
msg = Printer()

In [9]:
def generate_replay(
    model: BaseAlgorithm,
    eval_env: VecEnv,
    video_length: int,
    is_deterministic: bool,
    local_path: Path,
):
    """
    Generate a replay video of the agent
    :param model: trained model
    :param eval_env: environment used to evaluate the agent
    :param video_length: length of the video (in timesteps)
    :param is_deterministic: use deterministic or stochastic actions
    :param local_path: path of the local repository
    """
    # This is another temporary directory for video outputs
    # SB3 created a -step-0-to-... meta files as well as other
    # artifacts which we don't want in the repo.
    with tempfile.TemporaryDirectory() as tmpdirname:
        # Step 1: Create the VecVideoRecorder
        env = VecVideoRecorder(
            eval_env,
            tmpdirname,
            record_video_trigger=lambda x: x == 0,
            video_length=video_length,
            name_prefix="",
        )

        obs = env.reset()
        lstm_states = None
        episode_starts = np.ones((env.num_envs,), dtype=bool)

        try:
            for _ in range(video_length):
                action, lstm_states = model.predict(
                    obs,
                    state=lstm_states,
                    episode_start=episode_starts,
                    deterministic=is_deterministic,
                )
                obs, _, episode_starts, _ = env.step(action)

            # Save the video
            env.close()

            # Convert the video with x264 codec
            inp = env.video_recorder.path
            out = local_path
            os.system(f"ffmpeg -y -i {inp} -vcodec h264 {out}".format(inp, out))
            print(f"Video saved to: {out}")
        except KeyboardInterrupt:
            pass
        except Exception as e:
            msg.fail(str(e))
            # Add a message for video
            msg.fail(
                "We are unable to generate a replay of your agent"
            )

# **4. Training, Saving and Record the Videos**

In [10]:
import os

In [11]:
#create a directory to save the videos
video_dir = "/content/videos"
if not os.path.exists(video_dir):
    os.makedirs(video_dir)

In [12]:
env_id = "BipedalWalker-v3"
# Train and generate video at every 100000 steps, adjust the timesteps to your liking
for i in range(0, 2000000, 100000):
    model.learn(total_timesteps=100000)
    # Save the model
    model_name = "ppo-BipedalWalker-v3"
    model.save(model_name)
    video_name = f"replay_{i + 100000}.mp4"
    generate_replay(
        model=model,
        eval_env=DummyVecEnv([lambda: Monitor(gym.make(env_id, hardcore=True, render_mode="rgb_array"))]),
        video_length=1000,
        is_deterministic=True,
        local_path=os.path.join(video_dir, video_name)
    )

model_name = "ppo-BipedalWalker-v3"
model.save(model_name)


---------------------------------
| rollout/           |          |
|    ep_len_mean     | 363      |
|    ep_rew_mean     | -111     |
| time/              |          |
|    fps             | 2110     |
|    iterations      | 1        |
|    time_elapsed    | 15       |
|    total_timesteps | 32768    |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 558         |
|    ep_rew_mean          | -111        |
| time/                   |             |
|    fps                  | 1872        |
|    iterations           | 2           |
|    time_elapsed         | 34          |
|    total_timesteps      | 65536       |
| train/                  |             |
|    approx_kl            | 0.004189953 |
|    clip_fraction        | 0.0314      |
|    clip_range           | 0.2         |
|    entropy_loss         | -5.7        |
|    explained_variance   | -0.00111    |
|    learning_rate        | 0.

Moviepy - Done !
Moviepy - video ready /tmp/tmpe_rabw_g/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_100000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 604      |
|    ep_rew_mean     | -109     |
| time/              |          |
|    fps             | 2743     |
|    iterations      | 1        |
|    time_elapsed    | 11       |
|    total_timesteps | 32768    |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 715         |
|    ep_rew_mean          | -109        |
| time/                   |             |
|    fps                  | 2087        |
|    iterations           | 2           |
|    time_elapsed         | 31          |
|    total_timesteps      | 65536       |
| train/                  |             |
|    approx_kl            | 0.004628574 |
|    clip_fraction        | 0.0332      |
|    clip_range          

Moviepy - Done !
Moviepy - video ready /tmp/tmpet0sq4o8/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_200000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 750      |
|    ep_rew_mean     | -106     |
| time/              |          |
|    fps             | 2709     |
|    iterations      | 1        |
|    time_elapsed    | 12       |
|    total_timesteps | 32768    |
---------------------------------
----------------------------------------
| rollout/                |            |
|    ep_len_mean          | 837        |
|    ep_rew_mean          | -105       |
| time/                   |            |
|    fps                  | 2080       |
|    iterations           | 2          |
|    time_elapsed         | 31         |
|    total_timesteps      | 65536      |
| train/                  |            |
|    approx_kl            | 0.00410627 |
|    clip_fraction        | 0.0215     |
|    clip_range           | 0.2      

Moviepy - Done !
Moviepy - video ready /tmp/tmp6nu80d3v/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_300000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 944      |
|    ep_rew_mean     | -103     |
| time/              |          |
|    fps             | 2729     |
|    iterations      | 1        |
|    time_elapsed    | 12       |
|    total_timesteps | 32768    |
---------------------------------
----------------------------------------
| rollout/                |            |
|    ep_len_mean          | 1.11e+03   |
|    ep_rew_mean          | -98.5      |
| time/                   |            |
|    fps                  | 2085       |
|    iterations           | 2          |
|    time_elapsed         | 31         |
|    total_timesteps      | 65536      |
| train/                  |            |
|    approx_kl            | 0.01129375 |
|    clip_fraction        | 0.0917     |
|    clip_range           | 0.2      

Moviepy - Done !
Moviepy - video ready /tmp/tmp7r15vljr/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_400000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.09e+03 |
|    ep_rew_mean     | -89.4    |
| time/              |          |
|    fps             | 2840     |
|    iterations      | 1        |
|    time_elapsed    | 11       |
|    total_timesteps | 32768    |
---------------------------------
----------------------------------------
| rollout/                |            |
|    ep_len_mean          | 1.24e+03   |
|    ep_rew_mean          | -84.3      |
| time/                   |            |
|    fps                  | 2125       |
|    iterations           | 2          |
|    time_elapsed         | 30         |
|    total_timesteps      | 65536      |
| train/                  |            |
|    approx_kl            | 0.01023379 |
|    clip_fraction        | 0.0787     |
|    clip_range           | 0.2      

...

Moviepy - Done !
Moviepy - video ready /tmp/tmpe_hp7niz/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_1600000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.52e+03 |
|    ep_rew_mean     | 147      |
| time/              |          |
|    fps             | 2955     |
|    iterations      | 1        |
|    time_elapsed    | 11       |
|    total_timesteps | 32768    |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.52e+03    |
|    ep_rew_mean          | 145         |
| time/                   |             |
|    fps                  | 2264        |
|    iterations           | 2           |
|    time_elapsed         | 28          |
|    total_timesteps      | 65536       |
| train/                  |             |
|    approx_kl            | 0.008621457 |
|    clip_fraction        | 0.0986      |
|    clip_range         

Moviepy - Done !
Moviepy - video ready /tmp/tmpaznzhelg/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_1700000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.18e+03 |
|    ep_rew_mean     | 78.3     |
| time/              |          |
|    fps             | 2942     |
|    iterations      | 1        |
|    time_elapsed    | 11       |
|    total_timesteps | 32768    |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.31e+03    |
|    ep_rew_mean          | 105         |
| time/                   |             |
|    fps                  | 2243        |
|    iterations           | 2           |
|    time_elapsed         | 29          |
|    total_timesteps      | 65536       |
| train/                  |             |
|    approx_kl            | 0.006862997 |
|    clip_fraction        | 0.0713      |
|    clip_range         

Moviepy - Done !
Moviepy - video ready /tmp/tmprxdgh3n6/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_1800000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.53e+03 |
|    ep_rew_mean     | 147      |
| time/              |          |
|    fps             | 2914     |
|    iterations      | 1        |
|    time_elapsed    | 11       |
|    total_timesteps | 32768    |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.43e+03    |
|    ep_rew_mean          | 128         |
| time/                   |             |
|    fps                  | 2186        |
|    iterations           | 2           |
|    time_elapsed         | 29          |
|    total_timesteps      | 65536       |
| train/                  |             |
|    approx_kl            | 0.008797893 |
|    clip_fraction        | 0.109       |
|    clip_range         

Moviepy - Done !
Moviepy - video ready /tmp/tmp8s9zlzwy/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_1900000.mp4
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 1.6e+03  |
|    ep_rew_mean     | 166      |
| time/              |          |
|    fps             | 2926     |
|    iterations      | 1        |
|    time_elapsed    | 11       |
|    total_timesteps | 32768    |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 1.48e+03    |
|    ep_rew_mean          | 139         |
| time/                   |             |
|    fps                  | 2227        |
|    iterations           | 2           |
|    time_elapsed         | 29          |
|    total_timesteps      | 65536       |
| train/                  |             |
|    approx_kl            | 0.007888522 |
|    clip_fraction        | 0.0991      |
|    clip_range         

Moviepy - Done !
Moviepy - video ready /tmp/tmp4omqon_y/-step-0-to-step-1000.mp4
Video saved to: /content/videos/replay_2000000.mp4


In [13]:
with open(os.path.join(video_dir, "filelist.txt"), "w") as f:
    for i in range(0, 2000000, 100000):
        video_name = f"replay_{i + 100000}.mp4"
        f.write(f"file '{os.path.join(video_dir, video_name)}'\n")
# Concatenate all the videos into one
os.system(f"ffmpeg -f concat -safe 0 -i {os.path.join(video_dir, 'filelist.txt')} -c copy {os.path.join(video_dir, 'replay_all.mp4')}")

0

# **5. Visualize Final Video**

In [14]:
from IPython.display import HTML
from base64 import b64encode
mp4 = open('videos/replay_all.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=600 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

# **6. Evaluate the Model**

In [15]:
from stable_baselines3.common.evaluation import evaluate_policy

In [16]:
eval_env = Monitor(gym.make("BipedalWalker-v3"))
mean_reward, std_reward = evaluate_policy(model, eval_env, n_eval_episodes=10, deterministic=True)
print(f"mean_reward={mean_reward:.2f} +/- {std_reward}")

mean_reward=261.51 +/- 3.9297665708695195


# **7. Upload to HuggingFace**

In [18]:
from huggingface_sb3 import load_from_hub, package_to_hub
from huggingface_hub import notebook_login # To log to our Hugging Face account to be able to upload models to the Hub.

In [25]:
notebook_login()
!git config --global credential.helper store

In [27]:
env_id = "BipedalWalker-v3"
model_name = "ppo-BipedalWalker-v3"
model_architecture = "PPO"

repo_id = "Mahanthesh0r/BipedalWalker-RL" # Change with your repo id

## Define the commit message
commit_message = "Upload PPO BipedalWalker-v3 trained agent"

# Create the evaluation env and set the render_mode="rgb_array"
eval_env = DummyVecEnv([lambda: gym.make(env_id, hardcore=True, render_mode="rgb_array")])

package_to_hub(model=model, # trained model
               model_name=model_name, # The name of our trained model
               model_architecture=model_architecture, # The model architecture we used: in our case PPO
               env_id=env_id, # Name of the environment
               eval_env=eval_env,
               repo_id=repo_id,
               commit_message=commit_message)

ℹ This function will save, evaluate, generate a video of your agent,
create a model card and push everything to the hub. It might take up to 1min.
This is a work in progress: if you encounter a bug, please open an issue.


/usr/local/lib/python3.10/dist-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Saving video to /tmp/tmp9d8mdfno/-step-0-to-step-1000.mp4
Moviepy - Building video /tmp/tmp9d8mdfno/-step-0-to-step-1000.mp4.
Moviepy - Writing video /tmp/tmp9d8mdfno/-step-0-to-step-1000.mp4



Moviepy - Done !
Moviepy - video ready /tmp/tmp9d8mdfno/-step-0-to-step-1000.mp4
ℹ Pushing repo Mahanthesh0r/BipedalWalker-RL to the Hugging Face
Hub


policy.pth:   0%|          | 0.00/52.3k [00:00<?, ?B/s]

...

pytorch_variables.pth:   0%|          | 0.00/864 [00:00<?, ?B/s]

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

ppo-BipedalWalker-v3.zip:   0%|          | 0.00/176k [00:00<?, ?B/s]

ℹ Your model is pushed to the Hub. You can view your model here:
https://huggingface.co/Mahanthesh0r/BipedalWalker-RL/tree/main/


CommitInfo(commit_url='https://huggingface.co/Mahanthesh0r/BipedalWalker-RL/commit/6abba37274940a44ed1ed334e23ef915fb5ebee9', commit_message='Upload PPO BipedalWalker-v3 trained agent', commit_description='', oid='6abba37274940a44ed1ed334e23ef915fb5ebee9', pr_url=None, pr_revision=None, pr_num=None)

# **8. Load Models from HuggingFace (Optional)**

In [28]:
from huggingface_sb3 import load_from_hub
repo_id = "Mahanthesh0r/BipedalWalker-RL" # The repo_id
filename = "ppo-BipedalWalker-v3.zip" # The model filename.zip

checkpoint = load_from_hub(repo_id, filename)
model = PPO.load(checkpoint, print_system_info=True)

ppo-BipedalWalker-v3.zip:   0%|          | 0.00/176k [00:00<?, ?B/s]

== CURRENT SYSTEM INFO ==
- OS: Linux-6.1.85+-x86_64-with-glibc2.35 # 1 SMP PREEMPT_DYNAMIC Sun Apr 28 14:29:16 UTC 2024
- Python: 3.10.12
- Stable-Baselines3: 2.0.0a5
- PyTorch: 2.2.1+cu121
- GPU Enabled: True
- Numpy: 1.25.2
- Cloudpickle: 2.2.1
- Gymnasium: 0.28.1
- OpenAI Gym: 0.25.2

== SAVED MODEL SYSTEM INFO ==
- OS: Linux-6.1.85+-x86_64-with-glibc2.35 # 1 SMP PREEMPT_DYNAMIC Sun Apr 28 14:29:16 UTC 2024
- Python: 3.10.12
- Stable-Baselines3: 2.0.0a5
- PyTorch: 2.2.1+cu121
- GPU Enabled: True
- Numpy: 1.25.2
- Cloudpickle: 2.2.1
- Gymnasium: 0.28.1
- OpenAI Gym: 0.25.2



In [29]:
eval_env = Monitor(gym.make("BipedalWalker-v3", hardcore=True))
mean_reward, std_reward = evaluate_policy(model, eval_env, n_eval_episodes=10, deterministic=True)
print(f"mean_reward={mean_reward:.2f} +/- {std_reward}")

mean_reward=-65.27 +/- 47.54686592465245
